In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pydicom
from glob import glob
import cv2
from matplotlib import animation
from IPython import display


In [2]:
def standardize_pixel_array(dcm: pydicom.dataset.FileDataset) -> np.ndarray:
    """
    Source : https://www.kaggle.com/competitions/rsna-2023-abdominal-trauma-detection/discussion/427217
    """
    # Correct DICOM pixel_array if PixelRepresentation == 1.
    pixel_array = dcm.pixel_array
    if dcm.PixelRepresentation == 1:
        bit_shift = dcm.BitsAllocated - dcm.BitsStored
        dtype = pixel_array.dtype
        pixel_array = (pixel_array << bit_shift).astype(dtype) >> bit_shift

    intercept = float(dcm.RescaleIntercept) if hasattr(dcm, "RescaleIntercept") else 0
    slope = float(dcm.RescaleSlope) if hasattr(dcm, "RescaleSlope") else 1
    center = int(dcm.WindowCenter)
    width = int(dcm.WindowWidth)
    low = center - width / 2
    high = center + width / 2

    pixel_array = (pixel_array * slope) + intercept
    pixel_array = np.clip(pixel_array, low, high)
    return pixel_array

In [3]:
train_descriptions = pd.read_csv("../../input/rsna-2024-lumbar-spine-degenerative-classification/train_series_descriptions.csv")
train_coord_df = pd.read_csv("../../input/rsna-2024-lumbar-spine-degenerative-classification/train_label_coordinates.csv")
train_coord_df = train_coord_df.merge(train_descriptions, on=["series_id", "study_id"], how="left")
train_df = pd.read_csv("../../input/rsna-2024-lumbar-spine-degenerative-classification/train.csv")

In [4]:
anno_map = {
    "L1/L2": (255, 0, 0),
    "L2/L3": (0, 255, 0),
    "L3/L4": (0, 0, 255),
    "L4/L5": (0, 127, 127),
    "L5/S1": (127, 0, 127),
}

def get_volume(series_df: pd.DataFrame):
    volume = []
    img_paths = glob(f"../../input/rsna-2024-lumbar-spine-degenerative-classification/train_images/**/{series_df.series_id.iloc[0]}/*.dcm")
    for i in range(len(img_paths)):
        img_path = glob(f"../../input/rsna-2024-lumbar-spine-degenerative-classification/train_images/**/{series_df.series_id.iloc[0]}/{i+1}.dcm", recursive=True)[0]
        dicom = pydicom.dcmread(img_path)
        print(dicom.Rows, dicom.Columns)
        volume.append(standardize_pixel_array(dicom))
    volume = np.stack(volume)
    volume = (volume - volume.min()) / (volume.max() - volume.min() + 1e-6)
    volume = (volume * 255)#.astype(np.uint8)
    volume = np.stack([volume, volume, volume], -1)
    label = np.zeros_like(volume).astype(np.uint8)
    for i in range(len(volume)):
        annotation = series_df[series_df.instance_number == i + 1]
        for j in range(len(annotation)):
            label[i] = cv2.circle(label[i], (int(annotation.x.iloc[j]), int(annotation.y.iloc[j])), max(label.shape[1], label.shape[2]) // 25, color=anno_map[annotation.level.iloc[j]], thickness=-1)
    volume += label * 0.2
    return volume.clip(0, 255).astype(np.uint8)

In [5]:
idx = 2000

In [14]:
coord_label_num = train_coord_df.groupby("series_id").count().sort_values("series_id").study_id.to_numpy()
SCS = train_coord_df.groupby("series_id").head(1).sort_values("series_id").condition.to_numpy() 
series_id =  train_coord_df.groupby("series_id").head(1).sort_values("series_id").series_id
new_series_id = series_id[((SCS == "Spinal Canal Stenosis") & (coord_label_num == 5)) | ((SCS != "Spinal Canal Stenosis") & (coord_label_num == 10))]
new_train_coord_df = train_coord_df[train_coord_df.series_id.isin(new_series_id)].sort_values(by=["series_id", "level"]).reset_index(drop=True)
series_ids = new_train_coord_df.series_id.unique()
series_df = new_train_coord_df[new_train_coord_df.series_id == series_ids[idx]]
idx += 1
series_df

study_id   series_id  instance_number              condition  level  \
16575  1353517692  1619012544               12  Spinal Canal Stenosis  L1/L2   
16576  1353517692  1619012544               12  Spinal Canal Stenosis  L2/L3   
16577  1353517692  1619012544               12  Spinal Canal Stenosis  L3/L4   
16578  1353517692  1619012544               11  Spinal Canal Stenosis  L4/L5   
16579  1353517692  1619012544               11  Spinal Canal Stenosis  L5/S1   

                x           y series_description  
16575  232.747493  155.412844   Sagittal T2/STIR  
16576  224.998224  212.231250   Sagittal T2/STIR  
16577  219.945099  271.425000   Sagittal T2/STIR  
16578  228.508961  319.302752   Sagittal T2/STIR  
16579  240.879474  346.500000   Sagittal T2/STIR

In [15]:
# Animation
volume = get_volume(series_df)
print(volume.shape)
fig = plt.figure(figsize=(6, 6))
im = plt.imshow(volume[0])
def draw(i):
    im.set_array(volume[i])
    return [im]
anim = animation.FuncAnimation(
    fig, draw, frames=volume.shape[0], interval=200, blit=True
)
plt.close()
display.HTML(anim.to_jshtml())

448 462
448 462
448 462
448 462


448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
448 462
(20, 462, 448, 3)


In [9]:
train_df

study_id spinal_canal_stenosis_l1_l2 spinal_canal_stenosis_l2_l3  \
0        4003253                 Normal/Mild                 Normal/Mild   
1        4646740                 Normal/Mild                 Normal/Mild   
2        7143189                 Normal/Mild                 Normal/Mild   
3        8785691                 Normal/Mild                 Normal/Mild   
4       10728036                 Normal/Mild                 Normal/Mild   
...          ...                         ...                         ...   
1970  4282019580                 Normal/Mild                 Normal/Mild   
1971  4283570761                 Normal/Mild                 Normal/Mild   
1972  4284048608                 Normal/Mild                 Normal/Mild   
1973  4287160193                 Normal/Mild                    Moderate   
1974  4290709089                 Normal/Mild                 Normal/Mild   

     spinal_canal_stenosis_l3_l4 spinal_canal_stenosis_l4_l5  \
0                    Normal/Mild                 Normal/Mild   
1                       Moderate                      Severe   
2                    Normal/Mild                 Normal/Mild   
3                    Normal/Mild                 Normal/Mild   
4                    Normal/Mild                 Normal/Mild   
...                          ...                         ...   
1970                 Normal/Mild                 Normal/Mild   
1971                 Normal/Mild                 Normal/Mild   
1972                 Normal/Mild                      Severe   
1973                 Normal/Mild                 Normal/Mild   
1974                 Normal/Mild                 Normal/Mild   

     spinal_canal_stenosis_l5_s1 left_neural_foraminal_narrowing_l1_l2  \
0                    Normal/Mild                           Normal/Mild   
1                    Normal/Mild                           Normal/Mild   
2                    Normal/Mild                           Normal/Mild   
3                    Normal/Mild                           Normal/Mild   
4                    Normal/Mild                           Normal/Mild   
...                          ...                                   ...   
1970                 Normal/Mild                           Normal/Mild   
1971                 Normal/Mild                           Normal/Mild   
1972                 Normal/Mild                           Normal/Mild   
1973                 Normal/Mild                           Normal/Mild   
1974                 Normal/Mild                           Normal/Mild   

     left_neural_foraminal_narrowing_l2_l3  \
0                              Normal/Mild   
1                              Normal/Mild   
2                              Normal/Mild   
3                              Normal/Mild   
4                              Normal/Mild   
...                                    ...   
1970                           Normal/Mild   
1971                           Normal/Mild   
1972                           Normal/Mild   
1973                           Normal/Mild   
1974                           Normal/Mild   

     left_neural_foraminal_narrowing_l3_l4  \
0                              Normal/Mild   
1                              Normal/Mild   
2                              Normal/Mild   
3                              Normal/Mild   
4                              Normal/Mild   
...                                    ...   
1970                           Normal/Mild   
1971                           Normal/Mild   
1972                           Normal/Mild   
1973                           Normal/Mild   
1974                           Normal/Mild   

     left_neural_foraminal_narrowing_l4_l5  ...  \
0                                 Moderate  ...   
1                                 Moderate  ...   
2                              Normal/Mild  ...   
3                                 Moderate  ...   
4                              Normal/Mild  ...   
...                      